In [1]:
import motile
import networkx as nx

cells = [
        {"id": 0, "t": 0, "x": 1, "score": 0.8},
        {"id": 1, "t": 0, "x": 25, "score": 0.1},
        {"id": 2, "t": 1, "x": 0, "score": 0.3},
        {"id": 3, "t": 1, "x": 26, "score": 0.4},
        {"id": 4, "t": 2, "x": 2, "score": 0.6},
        {"id": 5, "t": 2, "x": 24, "score": 0.6},
        {"id": 6, "t": 2, "x": 35, "score": 0.7}
]

edges = [
    {"source": 0, "target": 2, "score": 0.9},
    {"source": 1, "target": 3, "score": 0.9},
    {"source": 0, "target": 3, "score": 0.5},
    {"source": 1, "target": 2, "score": 0.5},
    {"source": 2, "target": 4, "score": 0.7},
    {"source": 3, "target": 5, "score": 0.7},
    {"source": 2, "target": 5, "score": 0.3},
    {"source": 3, "target": 4, "score": 0.3},
    {"source": 3, "target": 6, "score": 0.8}
]

graph = nx.DiGraph()
graph.add_nodes_from([
    (cell["id"], cell)
    for cell in cells
])
graph.add_edges_from([
    (edge["source"], edge["target"], edge)
    for edge in edges
])

graph = motile.TrackGraph(graph)

In [2]:
from motile_toolbox.visualization import draw_track_graph

draw_track_graph(graph, alpha_attribute="score", label_attribute="score")

In [3]:
from motile.constraints import MaxParents, MaxChildren
from motile.costs import NodeSelection, EdgeSelection, Appear

solver = motile.Solver(graph)

solver.add_constraint(MaxParents(1))
solver.add_constraint(MaxChildren(1))

solver.add_cost(NodeSelection(weight=-1, attribute="score"))
solver.add_cost(EdgeSelection(weight=-1, attribute="score"))
solver.add_cost(Appear(constant=1))

solver.solve()

Could not create Gurobi backend: Gurobi error in ilpy/impl/solvers/GurobiBackend.cpp:22: PIP license can only be used from gurobipy interface


In [4]:
from motile_toolbox.visualization import draw_solution

draw_solution(graph, solver, label_attribute="score")

In [5]:
import ilpy
from motile.variables import NodeAppear


class LimitNumTracks(motile.constraints.Constraint):

  def __init__(self, num_tracks):
      self.num_tracks = num_tracks

  def instantiate(self, solver):

      appear_indicators = solver.get_variables(NodeAppear)

      constraint = ilpy.Constraint()
      for appear_indicator, index in appear_indicators.items():
        constraint.set_coefficient(index, 1.0)
      constraint.set_relation(ilpy.Relation.LessEqual)
      constraint.set_value(self.num_tracks)

      return [constraint]

In [6]:
solver.add_constraint(LimitNumTracks(1))
solver.solve()

Could not create Gurobi backend: Gurobi error in ilpy/impl/solvers/GurobiBackend.cpp:22: PIP license can only be used from gurobipy interface


In [7]:
draw_solution(graph, solver, label_attribute="score")

In [8]:
from motile.variables import NodeSelected


class SillyCost(motile.costs.Cost):

    def __init__(self, position_attribute, weight=1.0):
        self.position_attribute = position_attribute
        self.weight = motile.costs.Weight(weight)

    def apply(self, solver):
        node_indicators = solver.get_variables(NodeSelected)

        for node_indicator, index in node_indicators.items():

            # x position of the node
            x = solver.graph.nodes[node_indicator][self.position_attribute]

            # costs can be negative (i.e., a reward)
            costs = -x

            solver.add_variable_cost(index, costs, weight=self.weight)

In [9]:
print("Before adding silly cost:")
print(solver.get_variables(NodeSelected))

solver.add_cost(SillyCost('x', weight=0.02))

print("After adding silly cost:")
print(solver.get_variables(NodeSelected))

Before adding silly cost:
NodeSelected(0): cost=-0.800000011920929 value=1.0
NodeSelected(1): cost=-0.10000000149011612 value=0.0
NodeSelected(2): cost=-0.30000001192092896 value=1.0
NodeSelected(3): cost=-0.4000000059604645 value=0.0
NodeSelected(4): cost=-0.6000000238418579 value=1.0
NodeSelected(5): cost=-0.6000000238418579 value=0.0
NodeSelected(6): cost=-0.699999988079071 value=0.0
After adding silly cost:
NodeSelected(0): cost=-0.8199999928474426 value=1.0
NodeSelected(1): cost=-0.6000000238418579 value=0.0
NodeSelected(2): cost=-0.30000001192092896 value=1.0
NodeSelected(3): cost=-0.9199999570846558 value=0.0
NodeSelected(4): cost=-0.64000004529953 value=1.0
NodeSelected(5): cost=-1.0800000429153442 value=0.0
NodeSelected(6): cost=-1.399999976158142 value=0.0


In [10]:
solver.solve()

Could not create Gurobi backend: Gurobi error in ilpy/impl/solvers/GurobiBackend.cpp:22: PIP license can only be used from gurobipy interface


In [11]:
draw_solution(graph, solver, label_attribute="score")

In [12]:
import ilpy
from motile.variables import EdgeSelected


class EdgePairs(motile.variables.Variable):

  @staticmethod
  def instantiate(solver):

      edge_pairs = [
          (in_edge, out_edge)
          # for each node
          for node in solver.graph.nodes
          # for each pair of incoming and outgoing edge
          for in_edge in solver.graph.prev_edges[node]
          for out_edge in solver.graph.next_edges[node]
      ]

      return edge_pairs

  @staticmethod
  def instantiate_constraints(solver):

      edge_indicators = solver.get_variables(EdgeSelected)
      edge_pair_indicators = solver.get_variables(EdgePairs)

      constraints = []
      for (in_edge, out_edge), pair_index in edge_pair_indicators.items():

          in_edge_index = edge_indicators[in_edge]
          out_edge_index = edge_indicators[out_edge]

          # edge pair indicator = 1 <=> in edge = 1 and out edge = 1
          constraint = ilpy.Constraint()
          constraint.set_coefficient(pair_index, 2)
          constraint.set_coefficient(in_edge_index, -1)
          constraint.set_coefficient(out_edge_index, -1)
          constraint.set_relation(ilpy.Relation.LessEqual)
          constraint.set_value(0)
          constraints.append(constraint)

          constraint = ilpy.Constraint()
          constraint.set_coefficient(pair_index, -1)
          constraint.set_coefficient(in_edge_index, 1)
          constraint.set_coefficient(out_edge_index, 1)
          constraint.set_relation(ilpy.Relation.LessEqual)
          constraint.set_value(1)
          constraints.append(constraint)

      return constraints

In [13]:
class CurvatureCost(motile.costs.Cost):

    def __init__(self, position_attribute, weight=1.0):
        self.position_attribute = position_attribute
        self.weight = motile.costs.Weight(weight)

    def apply(self, solver):

        # get edge pair variables
        edge_pair_indicators = solver.get_variables(EdgePairs)

        for (in_edge, out_edge), index in edge_pair_indicators.items():

            in_offset = self.get_edge_offset(solver.graph, in_edge)
            out_offset = self.get_edge_offset(solver.graph, out_edge)

            curvature_cost = abs(out_offset - in_offset)

            solver.add_variable_cost(index, curvature_cost, self.weight)

    def get_edge_offset(self, graph, edge):

        pos_v = graph.nodes[edge[1]][self.position_attribute]
        pos_u = graph.nodes[edge[0]][self.position_attribute]

        return pos_v - pos_u

In [14]:
solver.add_cost(CurvatureCost('x', weight=0.1))
solver.solve()

Could not create Gurobi backend: Gurobi error in ilpy/impl/solvers/GurobiBackend.cpp:22: PIP license can only be used from gurobipy interface


In [15]:
print(solver.get_variables(EdgePairs))
draw_solution(graph, solver, label_attribute="score")

EdgePairs(((0, 2), (2, 4))): cost=0.30000001192092896 value=0.0
EdgePairs(((0, 2), (2, 5))): cost=2.5 value=0.0
EdgePairs(((1, 2), (2, 4))): cost=2.700000047683716 value=0.0
EdgePairs(((1, 2), (2, 5))): cost=4.900000095367432 value=0.0
EdgePairs(((0, 3), (3, 5))): cost=2.700000047683716 value=0.0
EdgePairs(((0, 3), (3, 4))): cost=4.900000095367432 value=0.0
EdgePairs(((0, 3), (3, 6))): cost=1.600000023841858 value=0.0
EdgePairs(((1, 3), (3, 5))): cost=0.30000001192092896 value=1.0
EdgePairs(((1, 3), (3, 4))): cost=2.5 value=0.0
EdgePairs(((1, 3), (3, 6))): cost=0.800000011920929 value=0.0
